In [32]:
from util import *
from glob import glob
import matplotlib.pyplot as plt
from shapely import wkt
from shapely.geometry import LineString, Polygon
pd.set_option("display.max_columns", None)

In [33]:
gdf = gpd.read_file(f"TEST/Southland_BigBay/BigBay_intersects.shp")
gdf["Date"] = pd.to_datetime(gdf.ShorelineI, dayfirst=True, format='mixed')
gdf["Year"] = gdf.Date.dt.year
gdf["YearsSinceBase"] = (gdf.Date - pd.Timestamp(1800, 1, 1)).dt.days / 365.25
gdf["YearsUntilFuture"] = (
    pd.Timestamp(2100, 1, 1) - gdf.Date
    ).dt.days / 365.25
gdf.Date = gdf.Date.astype(str)
gdf

#Why are distances negative? Because baseline is now offshore i.e zero is in the ocean?
#Do we need to ignore the sign? Erosion projection needs to show more negative distance (move onshore), while accretion needs to go in less negative (move offshore)

TransectID  ShorelineI  BaselineID  Distance    IntersectX  \
0            1.0  02/21/1967         0.0   -148.46  1.209014e+06   
1            1.0  03/07/2016         0.0   -117.57  1.208990e+06   
2            1.0  04/02/1953         0.0   -132.41  1.209001e+06   
3            1.0  01/31/2006         0.0    -88.35  1.208967e+06   
4            1.0  03/27/2020         0.0   -119.44  1.208991e+06   
...          ...         ...         ...       ...           ...   
6555        52.0  02/18/1988         0.0    -69.72  1.208650e+06   
6556        52.0  09/04/2013         0.0    -73.15  1.208653e+06   
6557        52.0  02/17/1975         0.0    -33.85  1.208622e+06   
6558        52.0  03/17/1979         0.0    -46.72  1.208632e+06   
6559        52.0  12/30/1984         0.0    -68.43  1.208649e+06   

        IntersectY  Uncertaint                                 geometry  \
0     5.079991e+06        5.62  POINT Z (1209013.659 5079991.251 0.000)   
1     5.080011e+06        2.28  POINT Z (1208989.755 5080010.808 0.000)   
2     5.080001e+06        3.79  POINT Z (1209001.241 5080001.411 0.000)   
3     5.080029e+06        2.32  POINT Z (1208967.135 5080029.316 0.000)   
4     5.080010e+06        2.30  POINT Z (1208991.200 5080009.626 0.000)   
...            ...         ...                                      ...   
6555  5.079633e+06        3.78  POINT Z (1208650.061 5079632.551 0.000)   
6556  5.079630e+06        2.30  POINT Z (1208652.753 5079630.436 0.000)   
6557  5.079655e+06        4.38  POINT Z (1208621.853 5079654.714 0.000)   
6558  5.079647e+06        3.77  POINT Z (1208631.976 5079646.761 0.000)   
6559  5.079633e+06        5.37  POINT Z (1208649.045 5079633.349 0.000)   

            Date  Year  YearsSinceBase  YearsUntilFuture  
0     1967-02-21  1967      167.134839        132.859685  
1     2016-07-03  2016      216.498289         83.496235  
2     1953-02-04  1953      153.089665        146.904860  
3     2006-01-31  2006      206.078029         93.916496  
4     2020-03-27  2020      220.229979         79.764545  
...          ...   ...             ...               ...  
6555  1988-02-18  1988      188.125941        111.868583  
6556  2013-04-09  2013      213.264887         86.729637  
6557  1975-02-17  1975      175.123888        124.870637  
6558  1979-03-17  1979      179.200548        120.793977  
6559  1984-12-30  1984      184.991102        115.003422  

[6560 rows x 12 columns]

In [34]:
lines = gpd.read_file("TEST/Southland_BigBay/BigBay_rates.shp")
lines

ObjectID_1  BaselineID  TransOrder  TransEdit  transectId  ShrCount  \
0           1.0         0.0         1.0        0.0         1.0      12.0   
1           2.0         0.0         2.0        0.0         2.0      12.0   
2           3.0         0.0         3.0        0.0         3.0      12.0   
3           4.0         0.0         4.0        0.0         4.0      12.0   
4           5.0         0.0         5.0        0.0         5.0      12.0   
..          ...         ...         ...        ...         ...       ...   
555       556.0         2.0       556.0        0.0       556.0      10.0   
556       557.0         2.0       557.0        0.0       557.0      10.0   
557       558.0         2.0       558.0        0.0       558.0      10.0   
558       559.0         2.0       559.0        0.0       559.0      10.0   
559       560.0         2.0       560.0        0.0       560.0      10.0   

      LRR   LR2   LCI    LSE   EPR  EPRunc    NSM    SCE   WLR   WR2   WCI  \
0    0.42  0.44  0.27  11.46  0.24    0.06  16.46  60.11  0.35  0.29  0.31   
1    0.38  0.40  0.27  11.49  0.25    0.06  16.76  56.84  0.30  0.23  0.32   
2    0.36  0.36  0.28  11.85  0.24    0.06  16.09  53.57  0.26  0.18  0.32   
3    0.33  0.31  0.28  12.02  0.23    0.06  15.54  49.64  0.23  0.15  0.32   
4    0.31  0.28  0.29  12.44  0.24    0.06  16.03  46.91  0.21  0.12  0.32   
..    ...   ...   ...    ...   ...     ...    ...    ...   ...   ...   ...   
555  0.63  0.76  0.23   7.09  0.82    0.11  43.69  44.52  0.56  0.80  0.19   
556  0.62  0.70  0.27   8.23  0.86    0.11  45.89  46.43  0.55  0.73  0.22   
557  0.55  0.67  0.25   7.60  0.76    0.11  40.10  40.10  0.49  0.69  0.22   
558  0.53  0.68  0.24   7.39  0.72    0.11  38.37  38.37  0.49  0.69  0.22   
559  0.55  0.65  0.27   8.11  0.74    0.11  39.52  39.72  0.50  0.67  0.23   

      WSE       TCD  calculated     Azimuth  \
0    4.24      0.00  129.289408  129.289408   
1    4.28     10.00  129.289406  129.289406   
2    4.35     20.00  129.289408  129.289408   
3    4.37     30.00  129.289407  129.289407   
4    4.38     40.00  129.289406  129.289406   
..    ...       ...         ...         ...   
555  1.66  15014.61   63.749759   63.749759   
556  1.96  15024.61   63.749759   63.749759   
557  1.92  15034.61   63.749757   63.749757   
558  1.92  15044.61   63.749757   63.749757   
559  2.04  15054.61   63.749757   63.749757   

                                              geometry  
0    LINESTRING Z (1208898.757 5080085.260 0.000, 1...  
1    LINESTRING Z (1208892.425 5080077.521 0.000, 1...  
2    LINESTRING Z (1208886.093 5080069.781 0.000, 1...  
3    LINESTRING Z (1208879.760 5080062.041 0.000, 1...  
4    LINESTRING Z (1208873.428 5080054.302 0.000, 1...  
..                                                 ...  
555  LINESTRING Z (1210642.816 5084179.832 0.000, 1...  
556  LINESTRING Z (1210647.239 5084170.864 0.000, 1...  
557  LINESTRING Z (1210651.662 5084161.895 0.000, 1...  
558  LINESTRING Z (1210656.085 5084152.926 0.000, 1...  
559  LINESTRING Z (1210660.508 5084143.957 0.000, 1...  

[560 rows x 22 columns]

In [35]:
def get_azimuth(line):
    p1, p2 = line.coords[1:]
    azimuth = math.degrees(math.atan2(p2[0]-p1[0], p2[1]-p1[1]))
    if azimuth < 0:
        azimuth += 360
    return azimuth
lines["Azimuth"] = lines.geometry.apply(get_azimuth)
lines.to_file("TEST/Southland_BigBay/BigBay_rates.shp")
lines

ObjectID_1  BaselineID  TransOrder  TransEdit  transectId  ShrCount  \
0           1.0         0.0         1.0        0.0         1.0      12.0   
1           2.0         0.0         2.0        0.0         2.0      12.0   
2           3.0         0.0         3.0        0.0         3.0      12.0   
3           4.0         0.0         4.0        0.0         4.0      12.0   
4           5.0         0.0         5.0        0.0         5.0      12.0   
..          ...         ...         ...        ...         ...       ...   
555       556.0         2.0       556.0        0.0       556.0      10.0   
556       557.0         2.0       557.0        0.0       557.0      10.0   
557       558.0         2.0       558.0        0.0       558.0      10.0   
558       559.0         2.0       559.0        0.0       559.0      10.0   
559       560.0         2.0       560.0        0.0       560.0      10.0   

      LRR   LR2   LCI    LSE   EPR  EPRunc    NSM    SCE   WLR   WR2   WCI  \
0    0.42  0.44  0.27  11.46  0.24    0.06  16.46  60.11  0.35  0.29  0.31   
1    0.38  0.40  0.27  11.49  0.25    0.06  16.76  56.84  0.30  0.23  0.32   
2    0.36  0.36  0.28  11.85  0.24    0.06  16.09  53.57  0.26  0.18  0.32   
3    0.33  0.31  0.28  12.02  0.23    0.06  15.54  49.64  0.23  0.15  0.32   
4    0.31  0.28  0.29  12.44  0.24    0.06  16.03  46.91  0.21  0.12  0.32   
..    ...   ...   ...    ...   ...     ...    ...    ...   ...   ...   ...   
555  0.63  0.76  0.23   7.09  0.82    0.11  43.69  44.52  0.56  0.80  0.19   
556  0.62  0.70  0.27   8.23  0.86    0.11  45.89  46.43  0.55  0.73  0.22   
557  0.55  0.67  0.25   7.60  0.76    0.11  40.10  40.10  0.49  0.69  0.22   
558  0.53  0.68  0.24   7.39  0.72    0.11  38.37  38.37  0.49  0.69  0.22   
559  0.55  0.65  0.27   8.11  0.74    0.11  39.52  39.72  0.50  0.67  0.23   

      WSE       TCD  calculated     Azimuth  \
0    4.24      0.00  129.289408  129.289408   
1    4.28     10.00  129.289406  129.289406   
2    4.35     20.00  129.289408  129.289408   
3    4.37     30.00  129.289407  129.289407   
4    4.38     40.00  129.289406  129.289406   
..    ...       ...         ...         ...   
555  1.66  15014.61   63.749759   63.749759   
556  1.96  15024.61   63.749759   63.749759   
557  1.92  15034.61   63.749757   63.749757   
558  1.92  15044.61   63.749757   63.749757   
559  2.04  15054.61   63.749757   63.749757   

                                              geometry  
0    LINESTRING Z (1208898.757 5080085.260 0.000, 1...  
1    LINESTRING Z (1208892.425 5080077.521 0.000, 1...  
2    LINESTRING Z (1208886.093 5080069.781 0.000, 1...  
3    LINESTRING Z (1208879.760 5080062.041 0.000, 1...  
4    LINESTRING Z (1208873.428 5080054.302 0.000, 1...  
..                                                 ...  
555  LINESTRING Z (1210642.816 5084179.832 0.000, 1...  
556  LINESTRING Z (1210647.239 5084170.864 0.000, 1...  
557  LINESTRING Z (1210651.662 5084161.895 0.000, 1...  
558  LINESTRING Z (1210656.085 5084152.926 0.000, 1...  
559  LINESTRING Z (1210660.508 5084143.957 0.000, 1...  

[560 rows x 22 columns]

In [36]:
gdf.Year.describe()

count    6560.000000
mean     1986.655488
std        22.005541
min      1952.000000
25%      1975.000000
50%      1985.000000
75%      2006.000000
max      2020.000000
Name: Year, dtype: float64

In [37]:
gdf.Distance.describe()

count    6560.000000
mean      -66.180852
std        28.458391
min      -248.790000
25%       -74.565000
50%       -59.115000
75%       -47.187500
max       -18.860000
Name: Distance, dtype: float64

In [38]:
def get_transect_metadata(transect_lines_shapefile: str):
    lines = gpd.read_file(transect_lines_shapefile)
    if "TransectID" in lines.columns:
        lines = lines.set_index("TransectID").sort_index()
    else:
        lines = lines.set_index("TransOrder").sort_index()
    lines["dist_to_neighbour"] = lines.distance(lines.shift(-1))
    breakpoints = lines.dist_to_neighbour[lines.dist_to_neighbour > 105]
    lines["group"] = pd.Series(range(len(breakpoints)), index=breakpoints.index)
    lines["group"] = lines.group.bfill().fillna(len(breakpoints)).astype(int)
    metadata = lines[["Azimuth", "group"]].to_dict(orient="index")
    return metadata

transect_metadata = get_transect_metadata(f"TEST/Southland_BigBay/BigBay_rates.shp")
transect_metadata

{1.0: {'Azimuth': 129.28940761342247, 'group': 0},
 2.0: {'Azimuth': 129.2894059239801, 'group': 0},
 3.0: {'Azimuth': 129.28940761342247, 'group': 0},
 4.0: {'Azimuth': 129.28940709717924, 'group': 0},
 5.0: {'Azimuth': 129.2894059239801, 'group': 0},
 6.0: {'Azimuth': 129.28940761342247, 'group': 0},
 7.0: {'Azimuth': 129.2894059239801, 'group': 0},
 8.0: {'Azimuth': 124.97100184884327, 'group': 0},
 9.0: {'Azimuth': 124.97100184884327, 'group': 0},
 10.0: {'Azimuth': 124.97100184884327, 'group': 0},
 11.0: {'Azimuth': 124.97100184884327, 'group': 0},
 12.0: {'Azimuth': 124.97100184884327, 'group': 0},
 13.0: {'Azimuth': 124.97100184884327, 'group': 0},
 14.0: {'Azimuth': 124.97100184884327, 'group': 0},
 15.0: {'Azimuth': 124.97100184884327, 'group': 0},
 16.0: {'Azimuth': 124.97100184884327, 'group': 0},
 17.0: {'Azimuth': 124.97100184884327, 'group': 0},
 18.0: {'Azimuth': 124.97100184884327, 'group': 0},
 19.0: {'Azimuth': 124.97100184884327, 'group': 0},
 20.0: {'Azimuth': 124.9

In [39]:
linear_models = fit(gdf, transect_metadata)
linear_models

TransectID     slope   intercept  group  r2_score        mae         mse  \
0           1.0  0.416216 -201.683212      0  0.441616   7.661099  109.483259   
1           2.0  0.381196 -193.274050      0  0.397919   7.649076  109.894809   
2           3.0  0.359762 -187.147133      0  0.356517   8.759539  116.764329   
3           4.0  0.332341 -180.683237      0  0.314662   9.610955  120.239979   
4           5.0  0.314755 -176.511773      0  0.277811  10.489988  128.726959   
..          ...       ...         ...    ...       ...        ...         ...   
555       556.0  0.632958 -165.172615      2  0.763267   5.131121   39.664041   
556       557.0  0.627512 -163.895142      2  0.701311   5.821505   53.532501   
557       558.0  0.547788 -146.944976      2  0.676706   5.485352   45.759963   
558       559.0  0.535130 -144.323944      2  0.678744   5.279930   43.264090   
559       560.0  0.551990 -148.207597      2  0.650534   5.749436   52.246886   

          rmse  
0    10.463425  
1    10.483072  
2    10.805754  
3    10.965399  
4    11.345790  
..         ...  
555   6.297939  
556   7.316591  
557   6.764611  
558   6.577544  
559   7.228201  

[560 rows x 8 columns]

In [64]:
#Run if rolling average is needed
linear_models = fit(gdf, transect_metadata)
rolled_slopes = linear_models.groupby("group").slope.rolling(10, min_periods=1).mean().dropna().reset_index(level=0)
linear_models.slope = rolled_slopes.slope
linear_models.dropna(inplace=True)
linear_models

TransectID     slope   intercept  group  r2_score       mae        mse  \
0           1.0  1.137493 -287.113293      0  0.899979  7.719117  81.226923   
1           2.0  1.116044 -271.071182      0  0.918585  7.778484  86.694893   
2           3.0  1.126207 -276.724950      0  0.950353  5.837518  56.063658   
3           4.0  1.130674 -276.507210      0  0.932981  5.839418  70.903340   
4           5.0  1.127845 -269.600165      0  0.954922  5.013590  44.378314   
..          ...       ...         ...    ...       ...       ...        ...   
100       101.0  0.164541  -61.579520      0  0.243565  6.791799  64.534554   
101       102.0  0.170545  -63.207372      0  0.259564  6.996329  67.737057   
102       103.0  0.177131  -69.212941      0  0.240615  8.333542  93.865278   
103       104.0  0.181155  -65.105831      0  0.239869  7.921248  80.745771   
104       105.0  0.158150  -13.362791      0  0.025587  5.978905  52.782057   

         rmse  
0    9.012598  
1    9.311009  
2    7.487567  
3    8.420412  
4    6.661705  
..        ...  
100  8.033340  
101  8.230253  
102  9.688409  
103  8.985865  
104  7.265126  

[105 rows x 8 columns]

In [41]:
#Changed coordinate function by making old_x and old_y negative 
def calculate_new_coordinates(old_x, old_y, bearing, distance):
    bearing_radians = math.radians(bearing)
    new_x = old_x + (distance * math.sin(bearing_radians))
    new_y = old_y + (distance * math.cos(bearing_radians))
    point = Point(new_x, new_y)
    assert not point.is_empty
    return point

#Removed other model equations and changed Azimuth addtion from 180 to 360 deg
def predict(
    df: pd.DataFrame,
    linear_models: pd.DataFrame,
    transect_metadata: dict,
):
    """_summary_

    Args:
        df (pd.DataFrame): dataframe with columns: TransectID, Date, Distance, YearsSinceBase
        linear_models (pd.DataFrame): dataframe with columns: TransectID, slope, intercept
        transect_metadata (dict): dict lookup of TransectID to Azimuth & group
        
    Returns:
        pd.DataFrame: resulting prediction points for the year 2100
    """
    results = []
    for i, row in linear_models.iterrows():
        transect_ID = row.TransectID
        transect_df = df[df.TransectID == transect_ID]
        latest_row = transect_df[transect_df.Date == transect_df["Date"].max()].iloc[0]
        future_year = int(row.get("FUTURE_YEAR", FUTURE_YEAR))
        result = row.to_dict()
        result.update({
            "TransectID": transect_ID,
            "BaselineID": latest_row.BaselineID,
            "group": row.group,
            "Year": future_year,
            "ocean_point": calculate_new_coordinates(
                latest_row.geometry.x,
                latest_row.geometry.y,
                transect_metadata[transect_ID]["Azimuth"] + 180,
                500,
            ),
        })
        
        model = "linear"
        slope = row.slope
        intercept = row.intercept

        predicted_distance = slope * (future_year - 1800) + intercept
        distance_difference = latest_row.Distance - predicted_distance
        result[f"{model}_model_point"] = calculate_new_coordinates(
            latest_row.geometry.x,
            latest_row.geometry.y,
            transect_metadata[transect_ID]["Azimuth"],
            distance_difference,
        )
        result[f"{model}_model_predicted_distance"] = predicted_distance
        result[f"{model}_model_distance"] = distance_difference
        results.append(result)
    results = gpd.GeoDataFrame(results)
    return results

In [42]:
results = predict(gdf, linear_models, transect_metadata)
results

TransectID     slope   intercept  group  r2_score        mae         mse  \
0           1.0  0.416216 -201.683212    0.0  0.441616   7.661099  109.483259   
1           2.0  0.381196 -193.274050    0.0  0.397919   7.649076  109.894809   
2           3.0  0.359762 -187.147133    0.0  0.356517   8.759539  116.764329   
3           4.0  0.332341 -180.683237    0.0  0.314662   9.610955  120.239979   
4           5.0  0.314755 -176.511773    0.0  0.277811  10.489988  128.726959   
..          ...       ...         ...    ...       ...        ...         ...   
555       556.0  0.632958 -165.172615    2.0  0.763267   5.131121   39.664041   
556       557.0  0.627512 -163.895142    2.0  0.701311   5.821505   53.532501   
557       558.0  0.547788 -146.944976    2.0  0.676706   5.485352   45.759963   
558       559.0  0.535130 -144.323944    2.0  0.678744   5.279930   43.264090   
559       560.0  0.551990 -148.207597    2.0  0.650534   5.749436   52.246886   

          rmse  BaselineID  Year  \
0    10.463425         0.0  2100   
1    10.483072         0.0  2100   
2    10.805754         0.0  2100   
3    10.965399         0.0  2100   
4    11.345790         0.0  2100   
..         ...         ...   ...   
555   6.297939         2.0  2100   
556   7.316591         2.0  2100   
557   6.764611         2.0  2100   
558   6.577544         2.0  2100   
559   7.228201         2.0  2100   

                                       ocean_point  \
0     POINT (1208604.2216800374 5080326.244798169)   
1     POINT (1208597.6214953572 5080318.724325307)   
2      POINT (1208591.759177119 5080310.600172546)   
3     POINT (1208585.8156848038 5080302.542416005)   
4      POINT (1208579.774952714 5080294.564213674)   
..                                             ...   
555  POINT (1210219.3853518984 5083971.0167788025)   
556    POINT (1210223.219432249 5083961.757681044)   
557   POINT (1210226.9865194224 5083952.465534683)   
558    POINT (1210231.291715014 5083943.438767716)   
559  POINT (1210236.0166048924 5083934.6189732775)   

                                linear_model_point  \
0     POINT (1208958.2129207018 5080036.615593516)   
1     POINT (1208953.5066825196 5080027.545545543)   
2    POINT (1208947.4067853957 5080019.6157579925)   
3     POINT (1208942.4405463687 5080010.758435923)   
4      POINT (1208936.9602347102 5080002.32171999)   
..                                             ...   
555   POINT (1210620.6500357948 5084168.900724728)   
556   POINT (1210625.3955686463 5084160.091110377)   
557   POINT (1210636.0660216473 5084154.203373942)   
558    POINT (1210641.542922894 5084145.754434428)   
559   POINT (1210644.9096024025 5084136.264837607)   

     linear_model_predicted_distance  linear_model_distance  
0                         -76.818262             -42.621738  
1                         -78.915345             -40.174655  
2                         -79.218390             -40.481610  
3                         -80.981057             -39.218943  
4                         -82.085147             -38.494853  
..                               ...                    ...  
555                        24.714812             -52.594812  
556                        24.358553             -51.578553  
557                        17.391381             -43.881381  
558                        16.214943             -42.574943  
559                        17.389331             -44.089331  

[560 rows x 14 columns]

In [43]:
results.set_geometry("linear_model_point", inplace=True, crs=2193)
results

TransectID     slope   intercept  group  r2_score        mae         mse  \
0           1.0  0.416216 -201.683212    0.0  0.441616   7.661099  109.483259   
1           2.0  0.381196 -193.274050    0.0  0.397919   7.649076  109.894809   
2           3.0  0.359762 -187.147133    0.0  0.356517   8.759539  116.764329   
3           4.0  0.332341 -180.683237    0.0  0.314662   9.610955  120.239979   
4           5.0  0.314755 -176.511773    0.0  0.277811  10.489988  128.726959   
..          ...       ...         ...    ...       ...        ...         ...   
555       556.0  0.632958 -165.172615    2.0  0.763267   5.131121   39.664041   
556       557.0  0.627512 -163.895142    2.0  0.701311   5.821505   53.532501   
557       558.0  0.547788 -146.944976    2.0  0.676706   5.485352   45.759963   
558       559.0  0.535130 -144.323944    2.0  0.678744   5.279930   43.264090   
559       560.0  0.551990 -148.207597    2.0  0.650534   5.749436   52.246886   

          rmse  BaselineID  Year  \
0    10.463425         0.0  2100   
1    10.483072         0.0  2100   
2    10.805754         0.0  2100   
3    10.965399         0.0  2100   
4    11.345790         0.0  2100   
..         ...         ...   ...   
555   6.297939         2.0  2100   
556   7.316591         2.0  2100   
557   6.764611         2.0  2100   
558   6.577544         2.0  2100   
559   7.228201         2.0  2100   

                                       ocean_point  \
0     POINT (1208604.2216800374 5080326.244798169)   
1     POINT (1208597.6214953572 5080318.724325307)   
2      POINT (1208591.759177119 5080310.600172546)   
3     POINT (1208585.8156848038 5080302.542416005)   
4      POINT (1208579.774952714 5080294.564213674)   
..                                             ...   
555  POINT (1210219.3853518984 5083971.0167788025)   
556    POINT (1210223.219432249 5083961.757681044)   
557   POINT (1210226.9865194224 5083952.465534683)   
558    POINT (1210231.291715014 5083943.438767716)   
559  POINT (1210236.0166048924 5083934.6189732775)   

                  linear_model_point  linear_model_predicted_distance  \
0    POINT (1208958.213 5080036.616)                       -76.818262   
1    POINT (1208953.507 5080027.546)                       -78.915345   
2    POINT (1208947.407 5080019.616)                       -79.218390   
3    POINT (1208942.441 5080010.758)                       -80.981057   
4    POINT (1208936.960 5080002.322)                       -82.085147   
..                               ...                              ...   
555  POINT (1210620.650 5084168.901)                        24.714812   
556  POINT (1210625.396 5084160.091)                        24.358553   
557  POINT (1210636.066 5084154.203)                        17.391381   
558  POINT (1210641.543 5084145.754)                        16.214943   
559  POINT (1210644.910 5084136.265)                        17.389331   

     linear_model_distance  
0               -42.621738  
1               -40.174655  
2               -40.481610  
3               -39.218943  
4               -38.494853  
..                     ...  
555             -52.594812  
556             -51.578553  
557             -43.881381  
558             -42.574943  
559             -44.089331  

[560 rows x 14 columns]

In [44]:
def prediction_results_to_line_polygon(results: gpd.GeoDataFrame):
    lines = []
    polygons = []
    for group_name, group_data in results.groupby(["BaselineID", "group"]):
        if len(group_data) > 1:
            # Convert the points to LineString
            line = LineString(list(group_data.geometry))
            lines.append(line)
            # Convert the points to a closed Polygon
            polygon = Polygon(list(group_data.geometry) + list(group_data.ocean_point)[::-1])
            polygons.append(polygon)
    lines = gpd.GeoSeries(lines, crs=2193)
    polygons = gpd.GeoSeries(polygons, crs=2193)
    return lines, polygons

In [45]:
lines, poly = prediction_results_to_line_polygon(results)
lines.to_file("Z:\DSAS\Region\Southland\BigBay\BigBay_projection_output_lines.shp")
poly.to_file("Z:\DSAS\Region\Southland\BigBay\BigBay_projection_output_polygon.shp")

In [46]:
lines, poly = prediction_results_to_line_polygon(results)
lines.to_file("TEST\Southland_BigBay\BigBay_projection_output_lines.shp")
poly.to_file("TEST\Southland_BigBay\BigBay_projection_output_polygon.shp")

In [47]:
m = poly.explore(tiles="Esri.WorldImagery")
gpd.GeoDataFrame(results.drop(columns=["ocean_point", "linear_model_point"]), geometry=results.linear_model_point).explore(m=m)
gdf.explore("Year", legend=True, m=m)